In [ ]:
from google.colab import drive
drive.mount('/content/gdrive/')
%cd /content/gdrive/'My Drive'/'Colab Notebooks'/
!pwd

Drive already mounted at /content/gdrive/; to attempt to forcibly remount, call drive.mount("/content/gdrive/", force_remount=True).
/content/gdrive/My Drive/Colab Notebooks
/content/gdrive/My Drive/Colab Notebooks


In [ ]:
import pandas as pd
pd.options.display.max_rows = None
pd.options.display.max_columns = None
import requests
import json
import csv
import logging
import time
from tqdm import *
import matplotlib.pyplot as plt
import numpy as np
import re
!pip install googletrans

In [ ]:
rent = pd.read_csv('sydney1.csv', encoding='utf-8', sep=',', header='infer')
rent.columns = ['link', 'title', 'address', 'property_type', 'bedrooms', 
  'bathrooms', 'residents', 'with_furniture', 'rental_price', 'rental_method', 'start_date', 
  'rental_period', 'facilities', 'surroundings', 'geo_location'] 

In [ ]:
rent.head(20)

link  \
0   https://www.awehome.com/au/sydney/detail-apart...   
1   https://www.awehome.com/au/sydney/detail-apart...   
2   https://www.awehome.com/au/sydney/detail-apart...   
3   https://www.awehome.com/au/sydney/detail-apart...   
4   https://www.awehome.com/au/sydney/detail-apart...   
5   https://www.awehome.com/au/sydney/detail-apart...   
6   https://www.awehome.com/au/sydney/detail-apart...   
7   https://www.awehome.com/au/sydney/detail-apart...   
8   https://www.awehome.com/au/sydney/detail-apart...   
9   https://www.awehome.com/au/sydney/detail-apart...   
10  https://www.awehome.com/au/sydney/detail-apart...   
11  https://www.awehome.com/au/sydney/detail-apart...   
12  https://www.awehome.com/au/sydney/detail-apart...   
13  https://www.awehome.com/au/sydney/detail-apart...   
14  https://www.awehome.com/au/sydney/detail-apart...   
15  https://www.awehome.com/au/sydney/detail-apart...   
16  https://www.awehome.com/au/sydney/detail-apart...   
17  https://www.awehome.com/au/sydney/detail-apart...   
18  https://www.awehome.com/au/sydney/detail-apart...   
19  https://www.awehome.com/au/sydney/detail-apart...   

                                  title  \
0          Burwood Grand全新apartment主卧出租   
1       悉尼 独立房间 出租3分钟 GS火车站 干净舒适次卧 价格可议   
2    【特价房间】Wolli Creek 火车站旁 全新高层大落地窗 两房   
3                   Camperdown豪华两房带高档家具   
4         悉尼Mascot次卧低价招租 包bill 带车位 交通方便   
5                        Ultimo小白楼 主卧出租   
6                  近悉大UTS唐人街新白楼两房两卫安保公寓   
7           悉尼chippendale三室一厅找室友低价出租一单间   
8            全新超值大两房一书房 大阳台窗户有庭院 特价限量出租   
9                  Forest Lodge两房两卫超大空间   
10       Darling Harbor 高层超广view两室 近期入住   
11         近期入住 长短租均可waterloo一房公寓出租 带家具   
12  Waterloo网红公寓楼，带独卫卧室超低价招租，主卧是爱干净的小姐姐   
13       Ultimo 极近UTS和悉大 2房2卫1厅房复式公寓 转租   
14           Zetland Rosebery新公寓大次卧独立卫浴   
15                     Zetland一室一厅书房540   
16    eastgarden Meriton近UNSW高级次卧，找女生室友   
17        UTS USYD darling harbour单间出租啦   
18       HurlstonePark160每周假期出租整洁干净别墅单间   
19               悉尼欧缇莫cloes旁两室主卧 250可全包   

                                              address property_type  bedrooms  \
0          43 Belmore St, Burwood NSW 2134, Australia            公寓         1   
1          18 Ebsworth St Zetland NSW 2017, Australia            公寓         3   
2    9 Brodie Spark Drive, Wolli Creek New South W...            公寓         2   
3    23-25 Larkin Street, Camperdown New South Wal...            公寓         2   
4             1 Church Ave Mascot NSW 2020, Australia            公寓         3   
5                   Ultimo Sydney NSW 2007, Australia            公寓         1   
6    69 Jones Street, Ultimo New South Wales 2007,...            公寓         2   
7     61-65 Regent St Chippendale NSW 2008, Australia            公寓         3   
8    906 Bourke Street, Zetland New South Wales 20...            公寓         2   
9      1 Scotsman St Forest Lodge NSW 2037, Australia            公寓         2   
10         Haymarket, New South Wales 2000, Australia            公寓         2   
11   11 Potter Street, Waterloo New South Wales 20...            公寓         1   
12          20 O'Dea Ave Waterloo NSW 2017, Australia            公寓         2   
13          58 Mountain St Ultimo NSW 2007, Australia            公寓         3   
14                 Zetland Sydney NSW 2017, Australia            公寓         1   
15      5 Hutchinson Walk Zetland NSW 2017, Australia            公寓         1   
16   15 Oscar Place, Eastgardens New South Wales 2...            公寓         2   
17         Haymarket, New South Wales 2000, Australia            公寓         2   
18   62 Crinan Street, Hurlstone Park New South Wa...            别墅         5   
19   558 Jones Street, Ultimo New South Wales 2007...            公寓         2   

    bathrooms  residents with_furniture  rental_price rental_method  \
0           1          1             包含           360         独立房间1   
1           2          3             包含           380         独立房间1   
2           2          2        

In [ ]:
rent.duplicated().sum()
rent = rent.drop_duplicates()

In [ ]:
rent.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2531 entries, 0 to 2530
Data columns (total 15 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   link            2531 non-null   object
 1   title           2531 non-null   object
 2   address         2531 non-null   object
 3   property_type   2531 non-null   object
 4   bedrooms        2531 non-null   int64 
 5   bathrooms       2531 non-null   int64 
 6   residents       2531 non-null   int64 
 7   with_furniture  2531 non-null   object
 8   rental_price    2531 non-null   int64 
 9   rental_method   2531 non-null   object
 10  start_date      2531 non-null   object
 11  rental_period   2512 non-null   object
 12  facilities      2529 non-null   object
 13  surroundings    2531 non-null   object
 14  geo_location    2531 non-null   object
dtypes: int64(4), object(11)
memory usage: 316.4+ KB


In [ ]:
rent.head(100)

link  \
0   https://www.awehome.com/au/sydney/detail-apart...   
1   https://www.awehome.com/au/sydney/detail-apart...   
2   https://www.awehome.com/au/sydney/detail-apart...   
3   https://www.awehome.com/au/sydney/detail-apart...   
4   https://www.awehome.com/au/sydney/detail-apart...   
5   https://www.awehome.com/au/sydney/detail-apart...   
6   https://www.awehome.com/au/sydney/detail-apart...   
7   https://www.awehome.com/au/sydney/detail-apart...   
8   https://www.awehome.com/au/sydney/detail-apart...   
9   https://www.awehome.com/au/sydney/detail-apart...   
10  https://www.awehome.com/au/sydney/detail-apart...   
11  https://www.awehome.com/au/sydney/detail-apart...   
12  https://www.awehome.com/au/sydney/detail-apart...   
13  https://www.awehome.com/au/sydney/detail-apart...   
14  https://www.awehome.com/au/sydney/detail-apart...   
15  https://www.awehome.com/au/sydney/detail-apart...   
16  https://www.awehome.com/au/sydney/detail-apart...   
17  https://www.awehome.com/au/sydney/detail-apart...   
18  https://www.awehome.com/au/sydney/detail-apart...   
19  https://www.awehome.com/au/sydney/detail-apart...   
20  https://www.awehome.com/au/sydney/detail-apart...   
21  https://www.awehome.com/au/sydney/detail-apart...   
22  https://www.awehome.com/au/sydney/detail-apart...   
23  https://www.awehome.com/au/sydney/detail-apart...   
24  https://www.awehome.com/au/sydney/detail-apart...   
25  https://www.awehome.com/au/sydney/detail-apart...   
26  https://www.awehome.com/au/sydney/detail-apart...   
27  https://www.awehome.com/au/sydney/detail-apart...   
28  https://www.awehome.com/au/sydney/detail-apart...   
29  https://www.awehome.com/au/sydney/detail-apart...   
30  https://www.awehome.com/au/sydney/detail-apart...   
31  https://www.awehome.com/au/sydney/detail-apart...   
32  https://www.awehome.com/au/sydney/detail-apart...   
33  https://www.awehome.com/au/sydney/detail-apart...   
34  https://www.awehome.com/au/sydney/detail-apart...   
35  https://www.awehome.com/au/sydney/detail-apart...   
36  https://www.awehome.com/au/sydney/detail-apart...   
37  https://www.awehome.com/au/sydney/detail-apart...   
38  https://www.awehome.com/au/sydney/detail-apart...   
39  https://www.awehome.com/au/sydney/detail-apart...   
40  https://www.awehome.com/au/sydney/detail-apart...   
41  https://www.awehome.com/au/sydney/detail-apart...   
42  https://www.awehome.com/au/sydney/detail-apart...   
43  https://www.awehome.com/au/sydney/detail-apart...   
44  https://www.awehome.com/au/sydney/detail-apart...   
45  https://www.awehome.com/au/sydney/detail-apart...   
46  https://www.awehome.com/au/sydney/detail-apart...   
47  https://www.awehome.com/au/sydney/detail-apart...   
48  https://www.awehome.com/au/sydney/detail-apart...   
49  https://www.awehome.com/au/sydney/detail-apart...   
50  https://www.awehome.com/au/sydney/detail-apart...   
51  https://www.awehome.com/au/sydney/detail-apart...   
52  https://www.awehome.com/au/sydney/detail-apart...   
53  https://www.awehome.com/au/sydney/detail-apart...   
54  https://www.awehome.com/au/sydney/detail-apart...   
55  https://www.awehome.com/au/sydney/detail-apart...   
56  https://www.awehome.com/au/sydney/detail-apart...   
57  https://www.awehome.com/au/sydney/detail-apart...   
58  https://www.awehome.com/au/sydney/detail-apart...   
59  https://www.awehome.com/au/sydney/detail-apart...   
60  https://www.awehome.com/au/sydney/detail-apart...   
61  https://www.awehome.com/au/sydney/detail-apart...   
62  https://www.awehome.com/au/sydney/detail-apart...   
63  https://www.awehome.com/au/sydney/detail-apart...   
64  https://www.awehome.com/au/sydney/detail-apart...   
65  https://www.awehome.com/au/sydney/detail-apart...   
66  https://www.awehome.com/au/sydney/detail-apart...   
67  https://www.awehome.com/au/sydney/detail-apart...   
68  https://www.awehome.com/au/sydney/detail-apart...   
69  https://www.awehome.com/au/sydney/detail-apart...   
70

In [ ]:
rent.reset_index(drop=True, inplace=True)

In [ ]:
null_columns=rent.columns[rent.isnull().any()]

In [ ]:
rent[null_columns].isnull().sum()

rental_period    19
facilities        2
dtype: int64

In [ ]:
print(rent[rent.isnull().any(axis=1)][null_columns])

     rental_period                                         facilities
123            NaN  洗衣机,冰箱,空调,WIFI,厨房,电梯,阳台,包bill,测试,超市,公园,餐馆,近cit...
124            NaN  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,近cit...
164            NaN  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,游泳池,...
181            NaN      洗衣机,冰箱,空调,WIFI,厨房,电梯,阳台,包bill,游泳池,健身房,火车站,公交站
190            NaN        洗衣机,冰箱,空调,WIFI,厨房,阳台,包bill,超市,公园,餐馆,游泳池,公交站
279            NaN  洗衣机,冰箱,WIFI,厨房,阳台,包bill,超市,公园,餐馆,近city,游泳池,健身房...
464            NaN  洗衣机,冰箱,空调,WIFI,厨房,电梯,阳台,超市,公园,餐馆,近city,游泳池,健身房...
473            NaN           洗衣机,冰箱,空调,WIFI,厨房,电梯,阳台,超市,公园,餐馆,火车站,公交站
582            NaN  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,超市,公园,餐馆,近city,游泳池,...
602            NaN  洗衣机,冰箱,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,健身房,近ci...
611            NaN  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,近cit...
636            NaN              洗衣机,冰箱,厨房,WIFI,包bill,阳台,超市,餐馆,公交站,火车站
664            NaN  洗衣机,冰箱,电视,WIFI,厨房,包bill,阳台,超市,公园,餐馆,近city,火车站,公交站
675            NaN  

In [ ]:
rent['address'] 

0              43 Belmore St, Burwood NSW 2134, Australia
1              18 Ebsworth St Zetland NSW 2017, Australia
2        9 Brodie Spark Drive, Wolli Creek New South W...
3        23-25 Larkin Street, Camperdown New South Wal...
4                 1 Church Ave Mascot NSW 2020, Australia
5                       Ultimo Sydney NSW 2007, Australia
6        69 Jones Street, Ultimo New South Wales 2007,...
7         61-65 Regent St Chippendale NSW 2008, Australia
8        906 Bourke Street, Zetland New South Wales 20...
9          1 Scotsman St Forest Lodge NSW 2037, Australia
10             Haymarket, New South Wales 2000, Australia
11       11 Potter Street, Waterloo New South Wales 20...
12              20 O'Dea Ave Waterloo NSW 2017, Australia
13              58 Mountain St Ultimo NSW 2007, Australia
14                     Zetland Sydney NSW 2017, Australia
15          5 Hutchinson Walk Zetland NSW 2017, Australia
16       15 Oscar Place, Eastgardens New South Wales 2...
17            

In [ ]:
logger = logging.getLogger("root")
logger.setLevel(logging.DEBUG)
# create console handler
ch = logging.StreamHandler()
ch.setLevel(logging.DEBUG)
logger.addHandler(ch)

In [ ]:
API_KEY = ""
# Backoff time sets how many minutes to wait between google pings when API limit is hit
BACKOFF_TIME = 30
# Set output file name here.
output_filename = 'transformed_sydney1.csv'
# Setinput file here
input_filename = "sydney1.csv"
# Specify the column name in input data that contains addresses here
address_column_name = "address"
# Return Full Google Results? If True, full JSON results from Google are included in output
RETURN_FULL_RESULTS = False

In [ ]:
# Form a list of addresses for geocoding:
# Make a big list of all of the addresses to be processed.
addresses = rent[address_column_name].tolist()

In [ ]:
def get_google_results(address, api_key=None, return_full_response=False):
    # Set up Geocoding url
    geocode_url = "https://maps.googleapis.com/maps/api/geocode/json?address={}".format(address)
    if api_key is not None:
        geocode_url = geocode_url + "&key={}".format(api_key)
        
    # Ping google for the reuslts:
    results = requests.get(geocode_url)
    # Results will be in JSON format - convert to dict using requests functionality
    results = results.json()

    # if there's no results or an error, return empty results.
    if len(results['results']) == 0:
        output = {
            "formatted_address" : None,
            "latitude": None,
            "longitude": None,
            "accuracy": None,
            "google_place_id": None,
            "type": None,
            "postcode": None
        }
    else:    
        answer = results['results'][0]
        output = {
            "formatted_address" : answer.get('formatted_address'),
            "latitude": answer.get('geometry').get('location').get('lat'),
            "longitude": answer.get('geometry').get('location').get('lng'),
            "accuracy": answer.get('geometry').get('location_type'),
            "google_place_id": answer.get("place_id"),
            "type": ",".join(answer.get('types')),
            "postcode": ",".join([x['long_name'] for x in answer.get('address_components') 
                                  if 'postal_code' in x.get('types')])
        }

   # Append some other details:    
    output['input_string'] = address
    output['number_of_results'] = len(results['results'])
    output['status'] = results.get('status')
    if return_full_response is True:
        output['response'] = results
    
    return output     

In [ ]:
test_result = get_google_results("Sydney, Australia", API_KEY, RETURN_FULL_RESULTS)

# Create a list to hold results
results = []
# Go through each address in turn
for address in addresses:
    # While the address geocoding is not finished:
    geocoded = False
    while geocoded is not True:
        # Geocode the address with google
        try:
            geocode_result = get_google_results(address, API_KEY, return_full_response=RETURN_FULL_RESULTS)
        except Exception as e:
            logger.exception(e)
            logger.error("Major error with {}".format(address))
            logger.error("Skipping!")
            geocoded = True
            
        # If we're over the API limit, backoff for a while and try again later.
        if geocode_result['status'] == 'OVER_QUERY_LIMIT':
            logger.info("Hit Query Limit! Backing off for a bit.")
            time.sleep(BACKOFF_TIME * 60) # sleep for 30 minutes
            geocoded = False
        else:
            # If we're ok with API use, save the results
            # Note that the results might be empty / non-ok - log this
            if geocode_result['status'] != 'OK':
                logger.warning("Error geocoding {}: {}".format(address, geocode_result['status']))
            logger.debug("Geocoded: {}: {}".format(address, geocode_result['status']))
            results.append(geocode_result)           
            geocoded = True

    # Print status every 100 addresses
    if len(results) % 100 == 0:
    	logger.info("Completed {} of {} address".format(len(results), len(addresses)))
            
    # Every 500 addresses, save progress to file(in case of a failure so you have something!)
    if len(results) % 500 == 0:
        pd.DataFrame(results).to_csv("{}_bak".format(output_filename))

# All done
logger.info("Finished geocoding all addresses")
# Write the full results to csv using the pandas library.
pd.DataFrame(results).to_csv(output_filename, encoding='utf8')

Geocoded:  43 Belmore St, Burwood NSW 2134, Australia: OK
Geocoded: 18 Ebsworth St Zetland NSW 2017, Australia: OK
Geocoded:  9 Brodie Spark Drive, Wolli Creek New South Wales 2205, Australia: OK
Geocoded:  23-25 Larkin Street, Camperdown New South Wales 2050, Australia: OK
Geocoded: 1 Church Ave Mascot NSW 2020, Australia: OK
Geocoded: Ultimo Sydney NSW 2007, Australia: OK
Geocoded:  69 Jones Street, Ultimo New South Wales 2007, Australia: OK
Geocoded: 61-65 Regent St Chippendale NSW 2008, Australia: OK
Geocoded:  906 Bourke Street, Zetland New South Wales 2017, Australia: OK
Geocoded: 1 Scotsman St Forest Lodge NSW 2037, Australia: OK
Geocoded:  Haymarket, New South Wales 2000, Australia: OK
Geocoded:  11 Potter Street, Waterloo New South Wales 2017, Australia: OK
Geocoded: 20 O'Dea Ave Waterloo NSW 2017, Australia: OK
Geocoded: 58 Mountain St Ultimo NSW 2007, Australia: OK
Geocoded: Zetland Sydney NSW 2017, Australia: OK
Geocoded: 5 Hutchinson Walk Zetland NSW 2017, Australia: OK
Ge

In [ ]:
transformed_address = pd.read_csv('transformed_sydney1.csv', encoding='utf-8', sep=',', header='infer')
rent[['formatted_address','latitude', 'longitude', 'postcode']] = transformed_address[['formatted_address','latitude','longitude', 'postcode']]

In [ ]:
rent=rent.drop('address', 1)

In [ ]:
rent.head(2)

link  \
0  https://www.awehome.com/au/sydney/detail-apart...   
1  https://www.awehome.com/au/sydney/detail-apart...   

                             title property_type  bedrooms  bathrooms  \
0     Burwood Grand全新apartment主卧出租            公寓         1          1   
1  悉尼 独立房间 出租3分钟 GS火车站 干净舒适次卧 价格可议            公寓         3          2   

   residents with_furniture  rental_price rental_method start_date  \
0          1             包含           360         独立房间1  2021/4/26   
1          3             包含           380         独立房间1         随时   

  rental_period                                         facilities  \
0          租期不限  洗衣机,空调,电梯,冰箱,WIFI,阳台,电视,厨房,包bill,超市,公园,餐馆,近cit...   
1          租期不限  洗衣机,冰箱,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,近city,火...   

                                        surroundings  \
0  <p id="searchview_per1" class="searchview_per1...   
1  <p id="searchview_per1" class="searchview_per1...   

                                        geo_location  \
0  43 Belmore St, Burwood NSW, Australia, 悉尼大学：\n...   
1  18 Ebsworth St Zetland NSW 2017, 悉尼大学：\n步行距离31...   

                             formatted_address   latitude   longitude postcode  
0   43 Belmore St, Burwood NSW 2134, Australia -33.878202  151.100688     2134  
1  18 Ebsworth St, Zetland NSW 2017, Australia -33.906217  151.204689     2017

In [ ]:
rent['property_type'].value_counts()

公寓    2266
别墅     217
其他      48
Name: property_type, dtype: int64

In [ ]:
rent.loc[(rent.property_type == '公寓'), 'property_type']='apartment'
rent['property_type'] = np.where((rent.property_type == '别墅'),'house',rent.property_type)
rent['property_type'].mask(rent['property_type'] == '其他', 'others', inplace=True)
rent.head(5)

link  \
0  https://www.awehome.com/au/sydney/detail-apart...   
1  https://www.awehome.com/au/sydney/detail-apart...   
2  https://www.awehome.com/au/sydney/detail-apart...   
3  https://www.awehome.com/au/sydney/detail-apart...   
4  https://www.awehome.com/au/sydney/detail-apart...   

                                title property_type  bedrooms  bathrooms  \
0        Burwood Grand全新apartment主卧出租     apartment         1          1   
1     悉尼 独立房间 出租3分钟 GS火车站 干净舒适次卧 价格可议     apartment         3          2   
2  【特价房间】Wolli Creek 火车站旁 全新高层大落地窗 两房     apartment         2          2   
3                 Camperdown豪华两房带高档家具     apartment         2          2   
4       悉尼Mascot次卧低价招租 包bill 带车位 交通方便     apartment         3          2   

   residents with_furniture  rental_price rental_method start_date  \
0          1             包含           360         独立房间1  2021/4/26   
1          3             包含           380         独立房间1         随时   
2          2             包含           700          整套房子         随时   
3          3             包含           850          整套房子         随时   
4          3             包含           300         独立房间1         随时   

  rental_period                                         facilities  \
0          租期不限  洗衣机,空调,电梯,冰箱,WIFI,阳台,电视,厨房,包bill,超市,公园,餐馆,近cit...   
1          租期不限  洗衣机,冰箱,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,近city,火...   
2          租期不限  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,近cit...   
3            半年  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,超市,公园,餐馆,近city,火车站,公交站   
4          租期不限  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,近cit...   

                                        surroundings  \
0  <p id="searchview_per1" class="searchview_per1...   
1  <p id="searchview_per1" class="searchview_per1...   
2  <p id="searchview_per1" class="searchview_per1...   
3  <p id="searchview_per1" class="searchview_per1...   
4  <p id="searchview_per1" class="searchview_per1...   

                                        geo_location  \
0  43 Belmore St, Burwood NSW, Australia, 悉尼大学：\n...   
1  18 Ebsworth St Zetland NSW 2017, 悉尼大学：\n步行距离31...   
2  9 Brodie Spark Drive, Wolli Creek New South Wa...   
3  23-25 Larkin Street, Camperdown New South Wale...   
4  1 Church Ave Mascot NSW 2020, 新南威尔士大学：\n步行距离48...   

                                   formatted_address   latitude   longitude  \
0         43 Belmore St, Burwood NSW 2134, Australia -33.878202  151.100688   
1        18 Ebsworth St, Zetland NSW 2017, Australia -33.906217  151.204689   
2  9 Brodie Spark Dr, Wolli Creek NSW 2205, Austr... -33.928240  151.154429   
3    23-25 Larkin St, Camperdown NSW 2050, Australia -33.885271  151.180533   
4           1 Church Ave, Mascot NSW 2020, Australia -33.922905  151.190807   

  postcode  
0     2134  
1     2017  
2     2205  
3     2050  
4     2020

In [ ]:
rent['with_furniture'].mask(rent['with_furniture'] == '包含', '1', inplace=True)
rent['with_furniture'].mask(rent['with_furniture'] == '不包含', '0', inplace=True)
rent.head(4)

link  \
0  https://www.awehome.com/au/sydney/detail-apart...   
1  https://www.awehome.com/au/sydney/detail-apart...   
2  https://www.awehome.com/au/sydney/detail-apart...   
3  https://www.awehome.com/au/sydney/detail-apart...   

                                title property_type  bedrooms  bathrooms  \
0        Burwood Grand全新apartment主卧出租     apartment         1          1   
1     悉尼 独立房间 出租3分钟 GS火车站 干净舒适次卧 价格可议     apartment         3          2   
2  【特价房间】Wolli Creek 火车站旁 全新高层大落地窗 两房     apartment         2          2   
3                 Camperdown豪华两房带高档家具     apartment         2          2   

   residents with_furniture  rental_price rental_method start_date  \
0          1              1           360         独立房间1  2021/4/26   
1          3              1           380         独立房间1         随时   
2          2              1           700          整套房子         随时   
3          3              1           850          整套房子         随时   

  rental_period                                         facilities  \
0          租期不限  洗衣机,空调,电梯,冰箱,WIFI,阳台,电视,厨房,包bill,超市,公园,餐馆,近cit...   
1          租期不限  洗衣机,冰箱,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,近city,火...   
2          租期不限  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,近cit...   
3            半年  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,超市,公园,餐馆,近city,火车站,公交站   

                                        surroundings  \
0  <p id="searchview_per1" class="searchview_per1...   
1  <p id="searchview_per1" class="searchview_per1...   
2  <p id="searchview_per1" class="searchview_per1...   
3  <p id="searchview_per1" class="searchview_per1...   

                                        geo_location  \
0  43 Belmore St, Burwood NSW, Australia, 悉尼大学：\n...   
1  18 Ebsworth St Zetland NSW 2017, 悉尼大学：\n步行距离31...   
2  9 Brodie Spark Drive, Wolli Creek New South Wa...   
3  23-25 Larkin Street, Camperdown New South Wale...   

                                   formatted_address   latitude   longitude  \
0         43 Belmore St, Burwood NSW 2134, Australia -33.878202  151.100688   
1        18 Ebsworth St, Zetland NSW 2017, Australia -33.906217  151.204689   
2  9 Brodie Spark Dr, Wolli Creek NSW 2205, Austr... -33.928240  151.154429   
3    23-25 Larkin St, Camperdown NSW 2050, Australia -33.885271  151.180533   

  postcode  
0     2134  
1     2017  
2     2205  
3     2050

In [ ]:
rent['rental_method'].value_counts()

独立房间1                1130
整套房子                 1063
独立房间1 - 主卧            175
床位1                   108
独立房间1 - 次卧             20
次卧 - 次卧                 6
床位1 - 主卧                5
主卧 - 主卧                 3
独立房间2                   3
床位1 - 次卧                3
独立房间1 - 客厅              2
床位1 - 客厅                2
主卧独立卫浴 - 主卧             1
标间 - 次卧                 1
2 - 次卧                  1
独卫次卧 - 次卧               1
包bill单间 拎包入住 - 次卧       1
超大主卧 - 主卧               1
1 - 次卧                  1
主卧出租 - 主卧               1
1 - 主卧                  1
房间A - 客厅                1
整套房子 - 主卧               1
Name: rental_method, dtype: int64

In [ ]:
rent.loc[(rent.rental_method == '主卧独立卫浴 - 主卧'), 'rental_method']='独立房间1 - 主卧'
rent.loc[(rent.rental_method == '独卫次卧 - 次卧'), 'rental_method']='独立房间1 - 次卧'
rent.loc[(rent.rental_method == '房间A - 客厅'), 'rental_method']='床位1'
rent.loc[(rent.rental_method == '1 - 主卧'), 'rental_method']='独立房间1 - 主卧'
rent.loc[(rent.rental_method == '标间 - 次卧'), 'rental_method']='独立房间1 - 次卧'
rent.loc[(rent.rental_method == '整套房子 - 主卧'), 'rental_method']='独立房间1 - 主卧'
rent.loc[(rent.rental_method == '包bill单间 拎包入住 - 次卧'), 'rental_method']='独立房间1 - 次卧'
rent.loc[(rent.rental_method == '主卧出租 - 主卧'), 'rental_method']='独立房间1 - 主卧'
rent.loc[(rent.rental_method == '1 - 次卧'), 'rental_method']='独立房间1 - 次卧'
rent.loc[(rent.rental_method == '超大主卧 - 主卧'), 'rental_method']='独立房间1 - 主卧'
rent.loc[(rent.rental_method == '2 - 次卧'), 'rental_method']='独立房间1 - 次卧'
rent.loc[(rent.rental_method == '独立房间1 - 客厅'), 'rental_method']='床位1'
rent.loc[(rent.rental_method == '床位1 - 客厅'), 'rental_method']='床位1'
rent.loc[(rent.rental_method == '主卧 - 主卧'), 'rental_method']='独立房间1 - 主卧'
rent.loc[(rent.rental_method == '床位1 - 次卧'), 'rental_method']='床位1'
rent.loc[(rent.rental_method == '独立房间2'), 'rental_method']='独立房间1'
rent.loc[(rent.rental_method == '床位1 - 主卧'), 'rental_method']='床位1'
rent.loc[(rent.rental_method == '次卧 - 次卧'), 'rental_method']='独立房间1 - 次卧'

In [ ]:
rent.loc[(rent.rental_method == '整套房子'), 'rental_method']='studio'
rent['rental_method'] = np.where((rent.rental_method == '独立房间1'),'seperate_room',rent.rental_method )
rent['rental_method'].mask(rent['rental_method'] == '独立房间1 - 主卧', 'master_room', inplace=True)
rent['rental_method'].mask(rent['rental_method'] == '独立房间1 - 次卧', 'secondary_room', inplace=True)
rent.loc[(rent.rental_method == '床位1'), 'rental_method']='1bed'

rent['rental_method'].value_counts()

seperate_room     1133
studio            1063
master_room        183
1bed               121
secondary_room      31
Name: rental_method, dtype: int64

In [ ]:
rent['start_date'] = pd.to_datetime(rent['start_date'], format='%Y-%m-%d', errors='ignore')
today = pd.to_datetime('today').strftime("%Y-%m-%d")
rent.loc[rent['start_date'] == '随时', 'start_date'] = today


In [ ]:

rent['start_date'] = pd.to_datetime(rent['start_date'])

rent['start_date'] = rent['start_date'].dt.strftime('%Y-%m-%d')


In [ ]:
rent.head(100)

link  \
0   https://www.awehome.com/au/sydney/detail-apart...   
1   https://www.awehome.com/au/sydney/detail-apart...   
2   https://www.awehome.com/au/sydney/detail-apart...   
3   https://www.awehome.com/au/sydney/detail-apart...   
4   https://www.awehome.com/au/sydney/detail-apart...   
5   https://www.awehome.com/au/sydney/detail-apart...   
6   https://www.awehome.com/au/sydney/detail-apart...   
7   https://www.awehome.com/au/sydney/detail-apart...   
8   https://www.awehome.com/au/sydney/detail-apart...   
9   https://www.awehome.com/au/sydney/detail-apart...   
10  https://www.awehome.com/au/sydney/detail-apart...   
11  https://www.awehome.com/au/sydney/detail-apart...   
12  https://www.awehome.com/au/sydney/detail-apart...   
13  https://www.awehome.com/au/sydney/detail-apart...   
14  https://www.awehome.com/au/sydney/detail-apart...   
15  https://www.awehome.com/au/sydney/detail-apart...   
16  https://www.awehome.com/au/sydney/detail-apart...   
17  https://www.awehome.com/au/sydney/detail-apart...   
18  https://www.awehome.com/au/sydney/detail-apart...   
19  https://www.awehome.com/au/sydney/detail-apart...   
20  https://www.awehome.com/au/sydney/detail-apart...   
21  https://www.awehome.com/au/sydney/detail-apart...   
22  https://www.awehome.com/au/sydney/detail-apart...   
23  https://www.awehome.com/au/sydney/detail-apart...   
24  https://www.awehome.com/au/sydney/detail-apart...   
25  https://www.awehome.com/au/sydney/detail-apart...   
26  https://www.awehome.com/au/sydney/detail-apart...   
27  https://www.awehome.com/au/sydney/detail-apart...   
28  https://www.awehome.com/au/sydney/detail-apart...   
29  https://www.awehome.com/au/sydney/detail-apart...   
30  https://www.awehome.com/au/sydney/detail-apart...   
31  https://www.awehome.com/au/sydney/detail-apart...   
32  https://www.awehome.com/au/sydney/detail-apart...   
33  https://www.awehome.com/au/sydney/detail-apart...   
34  https://www.awehome.com/au/sydney/detail-apart...   
35  https://www.awehome.com/au/sydney/detail-apart...   
36  https://www.awehome.com/au/sydney/detail-apart...   
37  https://www.awehome.com/au/sydney/detail-apart...   
38  https://www.awehome.com/au/sydney/detail-apart...   
39  https://www.awehome.com/au/sydney/detail-apart...   
40  https://www.awehome.com/au/sydney/detail-apart...   
41  https://www.awehome.com/au/sydney/detail-apart...   
42  https://www.awehome.com/au/sydney/detail-apart...   
43  https://www.awehome.com/au/sydney/detail-apart...   
44  https://www.awehome.com/au/sydney/detail-apart...   
45  https://www.awehome.com/au/sydney/detail-apart...   
46  https://www.awehome.com/au/sydney/detail-apart...   
47  https://www.awehome.com/au/sydney/detail-apart...   
48  https://www.awehome.com/au/sydney/detail-apart...   
49  https://www.awehome.com/au/sydney/detail-apart...   
50  https://www.awehome.com/au/sydney/detail-apart...   
51  https://www.awehome.com/au/sydney/detail-apart...   
52  https://www.awehome.com/au/sydney/detail-apart...   
53  https://www.awehome.com/au/sydney/detail-apart...   
54  https://www.awehome.com/au/sydney/detail-apart...   
55  https://www.awehome.com/au/sydney/detail-apart...   
56  https://www.awehome.com/au/sydney/detail-apart...   
57  https://www.awehome.com/au/sydney/detail-apart...   
58  https://www.awehome.com/au/sydney/detail-apart...   
59  https://www.awehome.com/au/sydney/detail-apart...   
60  https://www.awehome.com/au/sydney/detail-apart...   
61  https://www.awehome.com/au/sydney/detail-apart...   
62  https://www.awehome.com/au/sydney/detail-apart...   
63  https://www.awehome.com/au/sydney/detail-apart...   
64  https://www.awehome.com/au/sydney/detail-apart...   
65  https://www.awehome.com/au/sydney/detail-apart...   
66  https://www.awehome.com/au/sydney/detail-apart...   
67  https://www.awehome.com/au/sydney/detail-apart...   
68  https://www.awehome.com/au/sydney/detail-apart...   
69  https://www.awehome.com/au/sydney/detail-apart...   
70

In [ ]:
rent.loc[(rent.rental_period == '租期不限'), 'rental_period']='unlimited'
rent['rental_period'] = np.where((rent.rental_period == '半年'),'half_year',rent.rental_period)
rent['rental_period'].mask(rent['rental_period'] == '短租', 'short_term', inplace=True)
rent['rental_period'].mask(rent['rental_period'] == '一年及以上', 'oneyear_above', inplace=True)

rent['rental_period'].value_counts()

unlimited        1125
half_year         781
short_term        408
oneyear_above     198
Name: rental_period, dtype: int64

In [ ]:
columns = ['洗衣机','冰箱','电视','空调','WIFI','厨房','电梯','阳台','公寓周边','超市','公园','餐馆','近city','健身房','火车站','公交站','游泳池']
for item in columns:
  rent[item] = rent['facilities'].apply(
    lambda x: 1 if item in str(x) else 0)

In [ ]:
rent.head()

link  \
0  https://www.awehome.com/au/sydney/detail-apart...   
1  https://www.awehome.com/au/sydney/detail-apart...   
2  https://www.awehome.com/au/sydney/detail-apart...   
3  https://www.awehome.com/au/sydney/detail-apart...   
4  https://www.awehome.com/au/sydney/detail-apart...   

                                title property_type  bedrooms  bathrooms  \
0        Burwood Grand全新apartment主卧出租     apartment         1          1   
1     悉尼 独立房间 出租3分钟 GS火车站 干净舒适次卧 价格可议     apartment         3          2   
2  【特价房间】Wolli Creek 火车站旁 全新高层大落地窗 两房     apartment         2          2   
3                 Camperdown豪华两房带高档家具     apartment         2          2   
4       悉尼Mascot次卧低价招租 包bill 带车位 交通方便     apartment         3          2   

   residents with_furniture  rental_price  rental_method  start_date  \
0          1              1           360  seperate_room  2021-04-26   
1          3              1           380  seperate_room  2021-06-23   
2          2              1           700         studio  2021-06-23   
3          3              1           850         studio  2021-06-23   
4          3              1           300  seperate_room  2021-06-23   

  rental_period                                         facilities  \
0     unlimited  洗衣机,空调,电梯,冰箱,WIFI,阳台,电视,厨房,包bill,超市,公园,餐馆,近cit...   
1     unlimited  洗衣机,冰箱,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,近city,火...   
2     unlimited  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,近cit...   
3     half_year  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,超市,公园,餐馆,近city,火车站,公交站   
4     unlimited  洗衣机,冰箱,电视,空调,WIFI,厨房,电梯,阳台,包bill,超市,公园,餐馆,近cit...   

                                        surroundings  \
0  <p id="searchview_per1" class="searchview_per1...   
1  <p id="searchview_per1" class="searchview_per1...   
2  <p id="searchview_per1" class="searchview_per1...   
3  <p id="searchview_per1" class="searchview_per1...   
4  <p id="searchview_per1" class="searchview_per1...   

                                        geo_location  \
0  43 Belmore St, Burwood NSW, Australia, 悉尼大学：\n...   
1  18 Ebsworth St Zetland NSW 2017, 悉尼大学：\n步行距离31...   
2  9 Brodie Spark Drive, Wolli Creek New South Wa...   
3  23-25 Larkin Street, Camperdown New South Wale...   
4  1 Church Ave Mascot NSW 2020, 新南威尔士大学：\n步行距离48...   

                                   formatted_address   latitude   longitude  \
0         43 Belmore St, Burwood NSW 2134, Australia -33.878202  151.100688   
1        18 Ebsworth St, Zetland NSW 2017, Australia -33.906217  151.204689   
2  9 Brodie Spark Dr, Wolli Creek NSW 2205, Austr... -33.928240  151.154429   
3    23-25 Larkin St, Camperdown NSW 2050, Australia -33.885271  151.180533   
4           1 Church Ave, Mascot NSW 2020, Australia -33.922905  151.190807   

  postcode  洗衣机  冰箱  电视  空调  WIFI  厨房  电梯  阳台  公寓周边  超市  公园  餐馆  近city  健身房  \
0     2134    1   1   1   1     1   1   1   1     0   1   1   1      1    1   
1     2017    1   1   0   1     1   1   1   1     0   1   1   1      1    0   
2     2205    1   1   1   1     1   1   1   1     0   1   1   1      1    1   
3     2050    1   1   1   1     1   1   1   1     0   1   1   1      1    0   
4     2020    1   1   1   1     1   1   1   1     0   1   1   1      1    0   

   火车站  公交站  游泳池  
0    1    1    1  
1    1    1    0  
2    1    1    1  
3    1    1    0  
4    1    1    0

In [ ]:
rent.columns = ['link','title', 'property_type', 'bedrooms', 'bathrooms','residents', 'with_furniture', 'rental_price', 'rental_method', 'start_date', 'rental_period', 'facilities', 'surroundings', 'geo_location'
, 'formatted_address', 'latitude', 'longitude', 'postcode', 'washing_machine', 'refrigerator', 'Tv', 'air_conditioner','WIFI', 'kitchen', 'elevator','balcony', 'nearby', 'supermarket', 'park', 'restaurant', 'close_city', 'gym', 'train_station', 'bus_station', 'swimming_pool']

In [ ]:
rent['nearby'].value_counts()

rent=rent.drop(['facilities', 'nearby'], 1)

In [ ]:
rent['surroundings'].unique()

array(['<p id="searchview_per1" class="searchview_per1" style="font-weight: bold">超市<span style="font-weight: normal"></span><br>公园<span style="font-weight: normal"></span><br>餐馆<span style="font-weight: normal"></span><br>近city<span style="font-weight: normal"></span><br>游泳池<span style="font-weight: normal"></span><br>健身房<span style="font-weight: normal"></span><br>火车站<span style="font-weight: normal"></span><br>公交站<span style="font-weight: normal"></span><br></p>\n<p id="searchview_per2" class="searchview_per2" style="font-weight: bold">附近大学：悉尼大学 <span style="font-weight: normal"></span><br></p>\n',
       '<p id="searchview_per1" class="searchview_per1" style="font-weight: bold">超市<span style="font-weight: normal"></span><br>公园<span style="font-weight: normal"></span><br>餐馆<span style="font-weight: normal"></span><br>近city<span style="font-weight: normal"></span><br>火车站<span style="font-weight: normal"></span><br>公交站<span style="font-weight: normal">：3分钟公交站</span><br></p>\n<p id="se

In [ ]:
def remove_tags(string):
    result = re.sub('<.*?>','',string)
    return result
rent['surroundings']=rent['surroundings'].apply(lambda cw : remove_tags(cw))

In [ ]:
rent.head(10)

link  \
0  https://www.awehome.com/au/sydney/detail-apart...   
1  https://www.awehome.com/au/sydney/detail-apart...   
2  https://www.awehome.com/au/sydney/detail-apart...   
3  https://www.awehome.com/au/sydney/detail-apart...   
4  https://www.awehome.com/au/sydney/detail-apart...   
5  https://www.awehome.com/au/sydney/detail-apart...   
6  https://www.awehome.com/au/sydney/detail-apart...   
7  https://www.awehome.com/au/sydney/detail-apart...   
8  https://www.awehome.com/au/sydney/detail-apart...   
9  https://www.awehome.com/au/sydney/detail-apart...   

                                title property_type  bedrooms  bathrooms  \
0        Burwood Grand全新apartment主卧出租     apartment         1          1   
1     悉尼 独立房间 出租3分钟 GS火车站 干净舒适次卧 价格可议     apartment         3          2   
2  【特价房间】Wolli Creek 火车站旁 全新高层大落地窗 两房     apartment         2          2   
3                 Camperdown豪华两房带高档家具     apartment         2          2   
4       悉尼Mascot次卧低价招租 包bill 带车位 交通方便     apartment         3          2   
5                      Ultimo小白楼 主卧出租     apartment         1          1   
6                近悉大UTS唐人街新白楼两房两卫安保公寓     apartment         2          2   
7         悉尼chippendale三室一厅找室友低价出租一单间     apartment         3          2   
8          全新超值大两房一书房 大阳台窗户有庭院 特价限量出租     apartment         2          2   
9                Forest Lodge两房两卫超大空间     apartment         2          2   

   residents with_furniture  rental_price  rental_method  start_date  \
0          1              1           360  seperate_room  2021-04-26   
1          3              1           380  seperate_room  2021-06-23   
2          2              1           700         studio  2021-06-23   
3          3              1           850         studio  2021-06-23   
4          3              1           300  seperate_room  2021-06-23   
5          1              1           240           1bed  2021-06-23   
6          4              1           850         studio  2021-06-23   
7          4              1           360  seperate_room  2021-06-23   
8          4              1           800         studio  2021-06-23   
9          3              1           900         studio  2021-06-23   

   rental_period                                       surroundings  \
0      unlimited              超市公园餐馆近city游泳池健身房火车站公交站\n附近大学：悉尼大学 \n   
1      unlimited  超市公园餐馆近city火车站公交站：3分钟公交站\n附近大学：悉尼大学 3分钟 green ...   
2      unlimited  超市公园餐馆近city游泳池健身房火车站公交站\n附近大学：悉尼大学 附近大学：悉尼科技大学...   
3      half_year        超市公园餐馆近city火车站公交站\n附近大学：悉尼大学 附近大学：悉尼科技大学 \n   
4      unlimited  超市公园餐馆近city火车站公交站\n附近大学：新南威尔士大学 附近大学：悉尼科技大学 附近...   
5      half_year  超市：Coles，Woolworth，Aldi公园：Victoria餐馆近city：走路直达...   
6      half_year  超市公园餐馆近city游泳池健身房火车站公交站\n附近大学：悉尼科技大学 步行10分钟附近大...   
7      half_year  超市公园餐馆近city火车站公交站\n附近大学：悉尼大学 附近大学：悉尼科技大学 附近大学：...   
8      unlimited  超市公园餐馆火车站公交站\n附近大学：新南威尔士大学 附近大学：泰勒学院 附近大学：悉尼大学 \n   
9  oneyear_above  超市餐馆：小型购物商场近city公交站\n附近大学：悉尼大学 10min附近大学：悉尼科技大...   

                                        geo_location  \
0  43 Belmore St, Burwood NSW, Australia, 悉尼大学：\n...   
1  18 Ebsworth St Zetland NSW 2017, 悉尼大学：\n步行距离31...   
2  9 Brodie Spark Drive, Wolli Creek New South Wa...   
3  23-25 Larkin Street, Camperdown New South Wale...   
4  1 Church Ave Mascot NSW 2020, 新南威尔士大学：\n步行距离48...   
5  Ultimo Sydney NSW 2007, 悉尼大学：\n步行距离1701M， 坐车距离...   
6  69 Jones Street, Ultimo New South Wales 2007, ...   
7  61-65 Regent St Chippendale NSW 2008, 悉尼大学：\n步...   
8  906 Bourke Street, Zetland New South Wales 201...   
9  1 Scotsman St Forest Lodge NSW 2037, 悉尼大学：\n步行...   

                                   formatted_address   latitude   longitude  \
0         43 Belmore St, Burwood NSW 2134, Australia -33.878202  151.100688   
1        18 Ebsworth St, Zetland NSW 2017, Australia -33.906217  151.204689   
2  9 Brodie Spark Dr, Wolli Creek NSW 2205, Austr... -33.928240  151.154429   
3    23-25 Larkin St, Camperdown NSW 2050, Australia -33.885271  151.180533   
4      

In [ ]:
rent['postcode'].replace('', np.nan, inplace=True)
rent.dropna(subset=['postcode'], inplace= True) 
rent.head(100)

link  \
0   https://www.awehome.com/au/sydney/detail-apart...   
1   https://www.awehome.com/au/sydney/detail-apart...   
2   https://www.awehome.com/au/sydney/detail-apart...   
3   https://www.awehome.com/au/sydney/detail-apart...   
4   https://www.awehome.com/au/sydney/detail-apart...   
5   https://www.awehome.com/au/sydney/detail-apart...   
6   https://www.awehome.com/au/sydney/detail-apart...   
7   https://www.awehome.com/au/sydney/detail-apart...   
8   https://www.awehome.com/au/sydney/detail-apart...   
9   https://www.awehome.com/au/sydney/detail-apart...   
10  https://www.awehome.com/au/sydney/detail-apart...   
11  https://www.awehome.com/au/sydney/detail-apart...   
12  https://www.awehome.com/au/sydney/detail-apart...   
13  https://www.awehome.com/au/sydney/detail-apart...   
14  https://www.awehome.com/au/sydney/detail-apart...   
15  https://www.awehome.com/au/sydney/detail-apart...   
16  https://www.awehome.com/au/sydney/detail-apart...   
17  https://www.awehome.com/au/sydney/detail-apart...   
18  https://www.awehome.com/au/sydney/detail-apart...   
19  https://www.awehome.com/au/sydney/detail-apart...   
20  https://www.awehome.com/au/sydney/detail-apart...   
21  https://www.awehome.com/au/sydney/detail-apart...   
22  https://www.awehome.com/au/sydney/detail-apart...   
23  https://www.awehome.com/au/sydney/detail-apart...   
24  https://www.awehome.com/au/sydney/detail-apart...   
25  https://www.awehome.com/au/sydney/detail-apart...   
26  https://www.awehome.com/au/sydney/detail-apart...   
27  https://www.awehome.com/au/sydney/detail-apart...   
28  https://www.awehome.com/au/sydney/detail-apart...   
29  https://www.awehome.com/au/sydney/detail-apart...   
30  https://www.awehome.com/au/sydney/detail-apart...   
31  https://www.awehome.com/au/sydney/detail-apart...   
32  https://www.awehome.com/au/sydney/detail-apart...   
33  https://www.awehome.com/au/sydney/detail-apart...   
34  https://www.awehome.com/au/sydney/detail-apart...   
35  https://www.awehome.com/au/sydney/detail-apart...   
36  https://www.awehome.com/au/sydney/detail-apart...   
37  https://www.awehome.com/au/sydney/detail-apart...   
38  https://www.awehome.com/au/sydney/detail-apart...   
39  https://www.awehome.com/au/sydney/detail-apart...   
40  https://www.awehome.com/au/sydney/detail-apart...   
41  https://www.awehome.com/au/sydney/detail-apart...   
42  https://www.awehome.com/au/sydney/detail-apart...   
43  https://www.awehome.com/au/sydney/detail-apart...   
44  https://www.awehome.com/au/sydney/detail-apart...   
45  https://www.awehome.com/au/sydney/detail-apart...   
46  https://www.awehome.com/au/sydney/detail-apart...   
47  https://www.awehome.com/au/sydney/detail-apart...   
48  https://www.awehome.com/au/sydney/detail-apart...   
49  https://www.awehome.com/au/sydney/detail-apart...   
50  https://www.awehome.com/au/sydney/detail-apart...   
51  https://www.awehome.com/au/sydney/detail-apart...   
52  https://www.awehome.com/au/sydney/detail-apart...   
53  https://www.awehome.com/au/sydney/detail-apart...   
54  https://www.awehome.com/au/sydney/detail-apart...   
55  https://www.awehome.com/au/sydney/detail-apart...   
56  https://www.awehome.com/au/sydney/detail-apart...   
57  https://www.awehome.com/au/sydney/detail-apart...   
58  https://www.awehome.com/au/sydney/detail-apart...   
59  https://www.awehome.com/au/sydney/detail-apart...   
60  https://www.awehome.com/au/sydney/detail-apart...   
61  https://www.awehome.com/au/sydney/detail-apart...   
62  https://www.awehome.com/au/sydney/detail-apart...   
63  https://www.awehome.com/au/sydney/detail-apart...   
64  https://www.awehome.com/au/sydney/detail-apart...   
65  https://www.awehome.com/au/sydney/detail-apart...   
66  https://www.awehome.com/au/sydney/detail-apart...   
67  https://www.awehome.com/au/sydney/detail-apart...   
68  https://www.awehome.com/au/sydney/detail-apart...   
69  https://www.awehome.com/au/sydney/detail-apart...   
70

In [ ]:
rent['postcode'].replace('', np.nan, inplace=True)
rent.dropna(subset=['postcode'], inplace= True) 
rent.head(100)

link  \
0   https://www.awehome.com/au/sydney/detail-apart...   
1   https://www.awehome.com/au/sydney/detail-apart...   
2   https://www.awehome.com/au/sydney/detail-apart...   
3   https://www.awehome.com/au/sydney/detail-apart...   
4   https://www.awehome.com/au/sydney/detail-apart...   
5   https://www.awehome.com/au/sydney/detail-apart...   
6   https://www.awehome.com/au/sydney/detail-apart...   
7   https://www.awehome.com/au/sydney/detail-apart...   
8   https://www.awehome.com/au/sydney/detail-apart...   
9   https://www.awehome.com/au/sydney/detail-apart...   
10  https://www.awehome.com/au/sydney/detail-apart...   
11  https://www.awehome.com/au/sydney/detail-apart...   
12  https://www.awehome.com/au/sydney/detail-apart...   
13  https://www.awehome.com/au/sydney/detail-apart...   
14  https://www.awehome.com/au/sydney/detail-apart...   
15  https://www.awehome.com/au/sydney/detail-apart...   
16  https://www.awehome.com/au/sydney/detail-apart...   
17  https://www.awehome.com/au/sydney/detail-apart...   
18  https://www.awehome.com/au/sydney/detail-apart...   
19  https://www.awehome.com/au/sydney/detail-apart...   
20  https://www.awehome.com/au/sydney/detail-apart...   
21  https://www.awehome.com/au/sydney/detail-apart...   
22  https://www.awehome.com/au/sydney/detail-apart...   
23  https://www.awehome.com/au/sydney/detail-apart...   
24  https://www.awehome.com/au/sydney/detail-apart...   
25  https://www.awehome.com/au/sydney/detail-apart...   
26  https://www.awehome.com/au/sydney/detail-apart...   
27  https://www.awehome.com/au/sydney/detail-apart...   
28  https://www.awehome.com/au/sydney/detail-apart...   
29  https://www.awehome.com/au/sydney/detail-apart...   
30  https://www.awehome.com/au/sydney/detail-apart...   
31  https://www.awehome.com/au/sydney/detail-apart...   
32  https://www.awehome.com/au/sydney/detail-apart...   
33  https://www.awehome.com/au/sydney/detail-apart...   
34  https://www.awehome.com/au/sydney/detail-apart...   
35  https://www.awehome.com/au/sydney/detail-apart...   
36  https://www.awehome.com/au/sydney/detail-apart...   
37  https://www.awehome.com/au/sydney/detail-apart...   
38  https://www.awehome.com/au/sydney/detail-apart...   
39  https://www.awehome.com/au/sydney/detail-apart...   
40  https://www.awehome.com/au/sydney/detail-apart...   
41  https://www.awehome.com/au/sydney/detail-apart...   
42  https://www.awehome.com/au/sydney/detail-apart...   
43  https://www.awehome.com/au/sydney/detail-apart...   
44  https://www.awehome.com/au/sydney/detail-apart...   
45  https://www.awehome.com/au/sydney/detail-apart...   
46  https://www.awehome.com/au/sydney/detail-apart...   
47  https://www.awehome.com/au/sydney/detail-apart...   
48  https://www.awehome.com/au/sydney/detail-apart...   
49  https://www.awehome.com/au/sydney/detail-apart...   
50  https://www.awehome.com/au/sydney/detail-apart...   
51  https://www.awehome.com/au/sydney/detail-apart...   
52  https://www.awehome.com/au/sydney/detail-apart...   
53  https://www.awehome.com/au/sydney/detail-apart...   
54  https://www.awehome.com/au/sydney/detail-apart...   
55  https://www.awehome.com/au/sydney/detail-apart...   
56  https://www.awehome.com/au/sydney/detail-apart...   
57  https://www.awehome.com/au/sydney/detail-apart...   
58  https://www.awehome.com/au/sydney/detail-apart...   
59  https://www.awehome.com/au/sydney/detail-apart...   
60  https://www.awehome.com/au/sydney/detail-apart...   
61  https://www.awehome.com/au/sydney/detail-apart...   
62  https://www.awehome.com/au/sydney/detail-apart...   
63  https://www.awehome.com/au/sydney/detail-apart...   
64  https://www.awehome.com/au/sydney/detail-apart...   
65  https://www.awehome.com/au/sydney/detail-apart...   
66  https://www.awehome.com/au/sydney/detail-apart...   
67  https://www.awehome.com/au/sydney/detail-apart...   
68  https://www.awehome.com/au/sydney/detail-apart...   
69  https://www.awehome.com/au/sydney/detail-apart...   
70

In [ ]:
df2 = rent["formatted_address"].apply(lambda x: x.split(","))
df2.head(10)

0       [43 Belmore St,  Burwood NSW 2134,  Australia]
1      [18 Ebsworth St,  Zetland NSW 2017,  Australia]
2    [9 Brodie Spark Dr,  Wolli Creek NSW 2205,  Au...
3    [23-25 Larkin St,  Camperdown NSW 2050,  Austr...
4         [1 Church Ave,  Mascot NSW 2020,  Australia]
5                        [Ultimo NSW 2007,  Australia]
6          [69 Jones St,  Ultimo NSW 2007,  Australia]
7    [61-65 Regent St,  Chippendale NSW 2008,  Aust...
8       [906 Bourke St,  Zetland NSW 2017,  Australia]
9    [1 Scotsman St,  Forest Lodge NSW 2037,  Austr...
Name: formatted_address, dtype: object

In [ ]:
rent['state'] = df2.apply(lambda x: " ".join(x[-2].split()[-2]))
rent['state'].head(10)

0    N S W
1    N S W
2    N S W
3    N S W
4    N S W
5    N S W
6    N S W
7    N S W
8    N S W
9    N S W
Name: state, dtype: object

In [ ]:
rent['suburb'] = df2.apply(lambda x: " ".join(x[-2].split()[0:-2]))
rent['suburb'].head(10)

0         Burwood
1         Zetland
2     Wolli Creek
3      Camperdown
4          Mascot
5          Ultimo
6          Ultimo
7     Chippendale
8         Zetland
9    Forest Lodge
Name: suburb, dtype: object

In [ ]:
rent['state'].unique()
rent[rent.state.str.contains('N S W',case=False)]

link  \
0     https://www.awehome.com/au/sydney/detail-apart...   
1     https://www.awehome.com/au/sydney/detail-apart...   
2     https://www.awehome.com/au/sydney/detail-apart...   
3     https://www.awehome.com/au/sydney/detail-apart...   
4     https://www.awehome.com/au/sydney/detail-apart...   
5     https://www.awehome.com/au/sydney/detail-apart...   
6     https://www.awehome.com/au/sydney/detail-apart...   
7     https://www.awehome.com/au/sydney/detail-apart...   
8     https://www.awehome.com/au/sydney/detail-apart...   
9     https://www.awehome.com/au/sydney/detail-apart...   
10    https://www.awehome.com/au/sydney/detail-apart...   
11    https://www.awehome.com/au/sydney/detail-apart...   
12    https://www.awehome.com/au/sydney/detail-apart...   
13    https://www.awehome.com/au/sydney/detail-apart...   
14    https://www.awehome.com/au/sydney/detail-apart...   
15    https://www.awehome.com/au/sydney/detail-apart...   
16    https://www.awehome.com/au/sydney/detail-apart...   
17    https://www.awehome.com/au/sydney/detail-apart...   
18    https://www.awehome.com/au/sydney/detail-apart...   
19    https://www.awehome.com/au/sydney/detail-apart...   
20    https://www.awehome.com/au/sydney/detail-apart...   
21    https://www.awehome.com/au/sydney/detail-apart...   
22    https://www.awehome.com/au/sydney/detail-apart...   
23    https://www.awehome.com/au/sydney/detail-apart...   
24    https://www.awehome.com/au/sydney/detail-apart...   
25    https://www.awehome.com/au/sydney/detail-apart...   
26    https://www.awehome.com/au/sydney/detail-apart...   
27    https://www.awehome.com/au/sydney/detail-apart...   
28    https://www.awehome.com/au/sydney/detail-apart...   
29    https://www.awehome.com/au/sydney/detail-apart...   
30    https://www.awehome.com/au/sydney/detail-apart...   
31    https://www.awehome.com/au/sydney/detail-apart...   
32    https://www.awehome.com/au/sydney/detail-apart...   
33    https://www.awehome.com/au/sydney/detail-apart...   
34    https://www.awehome.com/au/sydney/detail-apart...   
35    https://www.awehome.com/au/sydney/detail-apart...   
36    https://www.awehome.com/au/sydney/detail-apart...   
37    https://www.awehome.com/au/sydney/detail-apart...   
38    https://www.awehome.com/au/sydney/detail-apart...   
39    https://www.awehome.com/au/sydney/detail-apart...   
40    https://www.awehome.com/au/sydney/detail-apart...   
41    https://www.awehome.com/au/sydney/detail-apart...   
42    https://www.awehome.com/au/sydney/detail-apart...   
43    https://www.awehome.com/au/sydney/detail-apart...   
44    https://www.awehome.com/au/sydney/detail-apart...   
45    https://www.awehome.com/au/sydney/detail-apart...   
46    https://www.awehome.com/au/sydney/detail-apart...   
47    https://www.awehome.com/au/sydney/detail-apart...   
48    https://www.awehome.com/au/sydney/detail-apart...   
49    https://www.awehome.com/au/sydney/detail-apart...   
50    https://www.awehome.com/au/sydney/detail-apart...   
51    https://www.awehome.com/au/sydney/detail-apart...   
52    https://www.awehome.com/au/sydney/detail-apart...   
53    https://www.awehome.com/au/sydney/detail-apart...   
54    https://www.awehome.com/au/sydney/detail-apart...   
55    https://www.awehome.com/au/sydney/detail-apart...   
56    https://www.awehome.com/au/sydney/detail-apart...   
57    https://www.awehome.com/au/sydney/detail-apart...   
58    https://www.awehome.com/au/sydney/detail-apart...   
59    https://www.awehome.com/au/sydney/detail-apart...   
60    https://www.awehome.com/au/sydney/detail-apart...   
61    https://www.awehome.com/au/sydney/detail-apart...   
62    https://www.awehome.com/au/sydney/detail-apart...   
63    https://www.awehome.com/au/sydney/detail-apart...   
64    https://www.awehome.com/au/sydney/detail-apart...   
65    https://www.awehome.com/au/sydney/detail-apart...   
66    https://www.awehome.com/au/sydney/detail-apart...   
67    https://www.awehome.com/au/sydney

In [ ]:
rent.to_csv('sydney_clean1.csv', sep=',', header='infer', encoding='utf-8-sig', index=0)